In [1]:
import numpy as np
import pandas as pd
import json
import os

import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as pltb

In [2]:
# Example of the data
df = pd.read_csv("data/bike_df.csv")
#print(df[["device.name", "timestamp", "x.acceleration", "y.acceleration", "z.acceleration", "engine.ignition.status.1"]].head().to_markdown(index=False))


In [ ]:
# First we need to remove nans from the dataset and then center the data.
df.dropna(inplace= True, subset=["x.acceleration", "y.acceleration", "z.acceleration"])

# We wil select an uncalibrated device to perfrom the analysis on
bike_df = df[df["device.name"] =="220902-3-3"]

# We remove all points where the bike is idle as the assumption is only true when the the bike is moving.
bike_df = bike_df[~((bike_df["movement.status"] ==False) | (bike_df["engine.ignition.status"] ==False) | (bike_df["din"] == 0))]

# Select only the acceleratin points
bike_df = bike_df[["x.acceleration", "y.acceleration", "z.acceleration"]]

# Center the data by subtracting the mean
bike_df_centered = bike_df.sub(bike_df.mean(axis=0), axis=1)

bike_df_centered.head()

In [9]:
# Performing the analysis



x.acceleration  y.acceleration  z.acceleration
104810       -0.041692        0.058761        2.716818
104842        0.113308       -0.082239        2.700818
104843        0.129308       -0.051239        2.716818
104844        0.238308       -0.113239        2.919818
104845        0.129308       -0.004239        2.747818

In [65]:
import math

# Interative visualisation of the uncalibrated data
fig = px.scatter_3d(bike_df_centered, x='x.acceleration', y='y.acceleration', z='z.acceleration')
fig.update_traces(marker_size = 1)

angle = 0 #math.pi / 4 # 45 degrees

name = "Uncalibrated Data"
camera = dict(
    #up=dict(x=0, y=math.cos(angle), z=math.sin(angle)),
    eye=dict(x=2, y=1, z=0.2)
)

fig.update_layout(scene_camera=camera, scene_dragmode='orbit', title=name)
fig.show()
fig.write_html("images/uncalibrated.html")

In [11]:
x_eye, y_eye, z_eye = 1.5, 1.5, 0

def rotate_z(x, y, z, theta):
    w = x+1j*y
    return np.real(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w)

frames=[]
for t in np.arange(0, 6.26, 0.01):
    xe, ye, ze = rotate_z(x_eye, y_eye, z_eye, -t)
    frames.append(go.Frame(dict(layout=dict(scene=dict(camera=dict(eye=dict(x=xe, y=ye, z=ze)))))))



fig = go.Figure(
    data=[go.Scatter3d(x=df["x.acceleration"],
    y=df["y.acceleration"],
    z=df["z.acceleration"],
    connectgaps=False,
    mode='markers',
    marker_size=1)],

    layout=go.Layout(
        xaxis=dict(range=[0, 5], autorange=False),
        yaxis=dict(range=[0, 5], autorange=False),
        title="Uncalibrated Data",
        scene=dict(
             xaxis_title='x acceleration',
             yaxis_title='y acceleration',
             zaxis_title='z acceleration'
        ),
        updatemenus=[dict(
            type="buttons",
            buttons=[dict(label="Play",
                          method="animate",
                          args=[None, {"frame": {"duration": 0.1}, "tranistion": {"duration": 0.1}}])])]
    ),
    frames=frames
)

fig.show()
#fig.write_html("images/uncalibrated.html")

In [27]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

fig = make_subplots(rows=1, cols=3)

fig.add_trace(
    go.Scatter(x=bike_df_centered["x.acceleration"], y=bike_df_centered["y.acceleration"],
        mode='markers',
        marker_size=1),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(x=bike_df_centered["x.acceleration"], y=bike_df_centered["z.acceleration"],
        mode='markers',
        marker_size=1),
    row=1, col=2
)

fig.add_trace(
    go.Scatter(x=bike_df_centered["y.acceleration"], y=bike_df_centered["z.acceleration"],
        mode='markers',
        marker_size=1),
    row=1, col=3
)

fig.update_layout(height=600, width=800, title_text="Side By Side Subplots")
fig.show()

In [ ]:
# vechile death data
df_death = pd.read_csv("data/List_of_countries_by_traffic-related_death_rate_1.csv", skiprows=[0])
df_death.rename(columns={'per 100,000\ninhabitants\nper year':'Deaths per 100k/year'}, inplace=True)
df_death = df_death[["Country/region", "Continent", "Deaths per 100k/year"]]
df_c = df_death[df_death["Continent"].isnull()].sort_values(by=["Deaths per 100k/year"], ascending=False)
print(df_c[["Country/region", "Deaths per 100k/year"]].to_markdown(index=False))

# find percentile of kenya globally
df_death["Percentile"] = df_death["Deaths per 100k/year"].rank(pct = True)
print(df_death.loc[df_death['Country/region'] == "Kenya"].to_markdown(index=False))

# 
df_a = df_death[df_death["Continent"] == "Africa"].sort_values(by=["Deaths per 100k/year"], ascending=False)
df_a["Percentile"] = df_a["Deaths per 100k/year"].rank(pct = True)
df_a.loc[df_death['Country/region'] == "Kenya"]